In [ ]:
# !pip install datasets

# !pip install simpletransformers

# !pip install --upgrade accelerate

# !pip uninstall -y transformers accelerate
# !pip install transformers accelerate

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# PREPARING DATASET

In [ ]:
"""A large crowd-sourced dataset for developing natural language interfaces for relational databases"""


import json
import os

import datasets


In [ ]:
_DESCRIPTION = """\
A large crowd-sourced dataset for developing natural language interfaces for relational databases
"""

_AGG_OPS = ["", "MAX", "MIN", "COUNT", "SUM", "AVG"]
_COND_OPS = ["=", ">", "<", "OP"]

In [ ]:
def _convert_to_human_readable(sel, agg, columns, conditions):


        rep = f"SELECT {_AGG_OPS[agg]} {columns[sel] if columns is not None else f'col{sel}'} FROM table"

        if conditions:
            rep += " WHERE " + " AND ".join([f"{columns[i]} {_COND_OPS[o]} {v}" for i, o, v in conditions])
        return " ".join(rep.split())

def _generate_examples(main_filepath, tables_filepath):
  """Yields examples."""

  # Build dictionary to table_ids:tables
  with open(tables_filepath, encoding="utf-8") as f:
      tables = [json.loads(line) for line in f]
      id_to_tables = {x["id"]: x for x in tables}
  rows = []
  ids =[]
  with open(main_filepath, encoding="utf-8") as f:
      for idx, line in enumerate(f):
          row = json.loads(line)
          row["table"] = id_to_tables[row["table_id"]]
          del row["table_id"]

          # Handle missing data
          row["table"]["page_title"] = row["table"].get("page_title", "")
          row["table"]["section_title"] = row["table"].get("section_title", "")
          row["table"]["caption"] = row["table"].get("caption", "")
          row["table"]["name"] = row["table"].get("name", "")
          row["table"]["page_id"] = str(row["table"].get("page_id", ""))

          # Fix row types
          row["table"]["rows"] = [[str(e) for e in r] for r in row["table"]["rows"]]

          # Get human-readable version
          row["sql"]["human_readable"] = _convert_to_human_readable(
              row["sql"]["sel"],
              row["sql"]["agg"],
              row["table"]["header"],
              row["sql"]["conds"],
          )

          # Restructure sql->conds
          # - wikiSQL provides a tuple [column_index, operator_index, condition]
          #   as 'condition' can have 2 types (float or str) we convert to dict
          for i in range(len(row["sql"]["conds"])):
              row["sql"]["conds"][i] = {
                  "column_index": row["sql"]["conds"][i][0],
                  "operator_index": row["sql"]["conds"][i][1],
                  "condition": str(row["sql"]["conds"][i][2]),
              }
              rows.append(row)
              ids.append(i)
      return rows


In [ ]:
main_filepath = "/content/drive/MyDrive/wikisqldata/train.jsonl"
tables_filepath = "/content/drive/MyDrive/wikisqldata/train.tables.jsonl"
train_da =_generate_examples(main_filepath, tables_filepath)
main_filepath = "/content/drive/MyDrive/wikisqldata/dev.jsonl"
tables_filepath = "/content/drive/MyDrive/wikisqldata/dev.tables.jsonl"
val_da =_generate_examples(main_filepath, tables_filepath)
main_filepath = "/content/drive/MyDrive/wikisqldata/test.jsonl"
tables_filepath = "/content/drive/MyDrive/wikisqldata/test.tables.jsonl"
test_da =_generate_examples(main_filepath, tables_filepath)

In [ ]:
print(len(train_da))
print(len(val_da))
print(len(test_da))

76729
11545
21846


In [ ]:
print(len(train_da))


[{'phase': 1,
  'question': 'Tell me what the notes are for South Australia ',
  'sql': {'sel': 5,
   'conds': [{'column_index': 3,
     'operator_index': 0,
     'condition': 'SOUTH AUSTRALIA'}],
   'agg': 0,
   'human_readable': 'SELECT Notes FROM table WHERE Current slogan = SOUTH AUSTRALIA'},
  'table': {'id': '1-1000181-1',
   'header': ['State/territory',
    'Text/background colour',
    'Format',
    'Current slogan',
    'Current series',
    'Notes'],
   'types': ['text', 'text', 'text', 'text', 'text', 'text'],
   'rows': [['Australian Capital Territory',
     'blue/white',
     'Yaa·nna',
     'ACT · CELEBRATION OF A CENTURY 2013',
     'YIL·00A',
     'Slogan screenprinted on plate'],
    ['New South Wales',
     'black/yellow',
     'aa·nn·aa',
     'NEW SOUTH WALES',
     'BX·99·HI',
     'No slogan on current series'],
    ['New South Wales',
     'black/white',
     'aaa·nna',
     'NSW',
     'CPX·12A',
     'Optional white slimline series'],
    ['Northern Territory'